In [100]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import warnings
import altair as alt
from vega_datasets import data

warnings.filterwarnings("ignore")
sns.set(rc={'figure.figsize':(10,7)})

Timely completion of the task.
● Providing visual encoding
● Task complexity, e.g., visualizations for multiple queries (3-5)/Including different
variety of visualizations (3-5) including Interactivity and animation/story-value/
exploiting tool strengths in some specific ways


4 queries
story value
exploiting tool strengths


In [19]:
train = pd.read_csv('../data/raw/train.csv')
test = pd.read_csv('../data/raw/test.csv')

In [20]:
train['year'] = train.month.str[:4].astype('int')
train['price_per_area'] = train['resale_price']/train['floor_area_sqm']
train['lease_duration'] = train['year']-train['lease_commence_date']
train['storey'] = (train.storey_range.str[-2:].astype('int') + train.storey_range.str[:2].astype('int'))/2
train['flat_type'] = train['flat_type'].str.replace('-', ' ') # there are some flat_type encoded as 4-room and 4 room

# flat_type as ordinal variables (either this or the one after)
train['flat_type_ord'] = train.flat_type.map({
    '1 room':1,
    '2 room':2,
    '3 room':3,
    '4 room':4,
    '5 room':5,
    'executive':6,
    'multi generation': 7
})

# region as dummies
#train = pd.get_dummies(train, columns=['flat_model', 'town', 'year'], drop_first=True)

# flat_type as categorical variable (either this or the one before)
# train = pd.get_dummies(train, columns=["flat_type"], drop_first=False)
# train.drop(columns = 'flat_type_multi generation') # dropping this since it is the least frequent among all flat types

#train.drop(columns = ['elevation', 'eco_category', 'flat_type', 'month'], inplace=True) # confirm drop
#train.drop(columns = ['storey_range', 'region', 'block', 'street_name', 'subzone', 'planning_area', 'lease_commence_date'], inplace=True) # to discuss

In [34]:
train

month           town flat_type block            street_name  \
0       2001-08      pasir ris    4 room   440      pasir ris drive 4   
1       2014-10        punggol    5 room  196B          punggol field   
2       2020-09       sengkang    5 room  404A          fernvale lane   
3       2000-10       clementi    3 room   375      clementi avenue 4   
4       2013-01    bukit batok    3 room   163  bukit batok street 11   
...         ...            ...       ...   ...                    ...   
431727  2005-03      woodlands    4 room   537     Woodlands Drive 16   
431728  2016-04       sengkang    4 room  410A          fernvale road   
431729  2011-01       tampines    3 room   829     tampines street 81   
431730  2013-05       sengkang    5 room   233       compassvale walk   
431731  2007-08  choa chu kang    4 room   121         Teck Whye Lane   

       storey_range  floor_area_sqm         flat_model   eco_category  \
0          01 to 03           118.0            model a  uncategorized   
1          10 to 12           110.0           improved  uncategorized   
2          01 to 03           112.0  premium apartment  uncategorized   
3          07 to 09            67.0     new generation  uncategorized   
4          07 to 09            73.0            model a  uncategorized   
...             ...             ...                ...            ...   
431727     01 to 03           101.0            model a  uncategorized   
431728     13 to 15            95.0  premium apartment  uncategorized   
431729     01 to 03            67.0     new generation  uncategorized   
431730     16 to 18           123.0           improved  uncategorized   
431731     01 to 03           104.0            model a  uncategorized   

        lease_commence_date  ...  elevation               subzone  \
0                      1989  ...        0.0       pasir ris drive   
1                      2003  ...        0.0         punggol field   
2                      2004  ...        0.0              fernvale   
3                      1980  ...        0.0        clementi north   
4                      1985  ...        0.0      bukit batok west   
...                     ...  ...        ...                   ...   
431727                 2000  ...        0.0       woodlands south   
431728                 2012  ...        0.0              fernvale   
431729                 1986  ...        0.0         tampines west   
431730                 1999  ...        0.0  sengkang town centre   
431731                 1989  ...        0.0             teck whye   

        planning_area             region resale_price  year  price_per_area  \
0           pasir ris        east region     209700.0  2001     1777.118644   
1             punggol  north-east region     402300.0  2014     3657.272727   
2            sengkang  north-east region     351000.0  2020     3133.928571   
3            clementi        west region     151200.0  2000     2256.716418   
4         bukit batok        west region     318600.0  2013     4364.383562   
...               ...                ...          ...   ...             ...   
431727      woodlands       north region     238500.0  2005     2361.386139   
431728       sengkang  north-east region     376200.0  2016     3960.000000   
431729       tampines        east region     255600.0  2011     3814.925373   
431730       sengkang  north-east region     508500.0  2013     4134.146341   
431731  choa chu kang        west region     162000.0  2007     1557.692308   

        lease_duration  storey  flat_type_ord  
0                   12     2.0              4  
1                   11    11.0              5  
2                   16     2.0              5  
3                   20     8.0              3  
4                   28     8.0              3  
...                ...     ...            ...  
431727               5     2.0              4  
431728               4    14.0              4  
431729              25     2.0              3 

what kind of data do i want to show

1. change in housing price across room types over time
change in area of room types sold

2. price change for housing areas -> overlay map?

3. 



In [36]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## Data Exploration

In [44]:
ptrain = train[0:2000]

In [115]:
# put in asia financial crisis 2007-2008
# https://www.srx.com.sg/cooling-measures#:~:text=These%20policies%20are%20often%20referred,'Property%20Market%20Cooling%20Measures'.&text=ABSD%20was%20first%20introduced%20on,escalation%20of%20residential%20property%20prices.

source2 = [{
            "start": "2007",
            "end": "2008",
            "event": "Global Financial Crisis"
          },
          {
            "start": "2012",
            "end": "2013",
            "event": "Mortgage rate reduced from 35-25"
          }]
source2 = alt.pd.DataFrame(source2)
rect = alt.Chart(source2).mark_rect().encode(
    x='start:O',
    x2='end:O',
    color='event:N'
)
p1 = train.groupby(["flat_type", "year"]).mean().reset_index()
line = alt.Chart(p1).mark_line().encode(
    x='year:O',
    y='resale_price',
    color='flat_type:N'
)

rect+line


# marks are the lines
# channels are the colors -> mark our key events as bars for comparison
# differet color hue for each flat type
# y axis is quantitative
# x axis is ordinal 

alt.LayerChart(...)

In [ ]:
# y axis quantitative, x axis ordinal
# boxplot and whiskers to show range
# interactivity -> select town to study the price across levels
# some areas, storey dont matter as much woodlands/ tampines
# some area it does, bishan, marine parade
train2 = train.groupby('subzone')

In [136]:
alt.Chart(train[train['town']=='clementi']).mark_boxplot().encode(
    x='storey_range:O',
    y='resale_price',
)

alt.Chart(...)

In [107]:
# filter by year
region_price=ptrain.groupby('subzone').mean().reset_index()[['subzone', 'latitude','longitude']]
counts = ptrain.groupby('subzone').count().reset_index()[['subzone', 'month']]
counts['count'] = counts['month']
count_df = region_price.join(counts, lsuffix='l', rsuffix='r')

In [112]:
# where got alot of transactions
alt.Chart(count_df).mark_point().encode(
    alt.X('latitude',
        scale=alt.Scale(
            domain=(1.26, 1.45),
            clamp=True
        )
    ),
    alt.Y('longitude',
        scale=alt.Scale(
            domain=(103.65, 104),
            clamp=True
        )
    ),
    alt.Size('count:Q', scale=alt.Scale(scheme='darkred')),
    alt.Color('count:Q', scale=alt.Scale(scheme='darkred', reverse=True))
)
# lat long quantitative
# marks are the circles -> 2d area and color illuminance increases with count
# shows areas where transactions are frequent
# interactivity (years)

alt.Chart(...)

In [114]:
# filter by year
region_price=ptrain.groupby('subzone').mean()
alt.Chart(region_price).mark_point().encode(
    alt.X('latitude',
        scale=alt.Scale(
            domain=(1.26, 1.45),
            clamp=True
        )
    ),
    alt.Y('longitude',
        scale=alt.Scale(
            domain=(103.65, 104),
            clamp=True
        )
    ),
    alt.Color('resale_price:Q', scale=alt.Scale(scheme='darkred', reverse=True)),
    alt.Size('resale_price:Q')
)
# lat long quantitative
# marks are the circles -> 2d area and color illuminance increases with count
# shows areas where transactions are frequent
# interactivity (years)

alt.Chart(...)